In [1]:
import pandas as pd

from datetime import datetime
import time

import json
import os

import pandas as pd
import matplotlib.pyplot as plt

import plotly.graph_objects as go
import plotly.offline as pyo

In [2]:
DATA_DIR = f'../GeneratedData/'
SAVE_DIR = f'../GeneratedData/Total/'

In [3]:
nft_list = [folder_name for folder_name in os.listdir(DATA_DIR) if (folder_name != '.DS_Store') and (folder_name != 'Total')]
for nft_name in nft_list:
    for file_name in os.listdir(DATA_DIR+nft_name):
        if '.json' in file_name:
            print(file_name)
            
if not os.path.exists(SAVE_DIR):
    os.mkdir(SAVE_DIR)

BEANZ.json
ContractTxn_MetaKongz.json


In [4]:
from collections import defaultdict
import datetime
import plotly.graph_objs as go
import os
import json

DATA_DIR = f'../GeneratedData/'
nft_list = [folder_name for folder_name in os.listdir(DATA_DIR) if (folder_name != '.DS_Store') and (folder_name != 'Total')]

def get_daily_transaction_volume(txn_list):
    daily_transaction_count = defaultdict(int)

    for txn in txn_list:
        date = datetime.datetime.fromtimestamp(txn['timestamp']).strftime('%Y-%m-%d')
        daily_transaction_count[date] += 1

    return daily_transaction_count

fig = go.Figure()

for nft_name in nft_list:
    for file_name in os.listdir(DATA_DIR + nft_name):
        if '.json' in file_name:
            with open(DATA_DIR + nft_name + "/" + file_name,'r') as file:
                json_data = file.read()
            txn_list = json.loads(json_data)
            
            # Calculate daily transaction volume for each NFT collection
            daily_txn_volume = get_daily_transaction_volume(txn_list)

            # Sort the result
            dates, volumes = zip(*sorted(daily_txn_volume.items()))

            # Add the transaction volume of each NFT collection to the graph
            fig.add_trace(go.Scatter(x=dates, y=volumes, mode='lines', name=nft_name))

# Set the title and axis names of the graph
fig.update_layout(
    title="Daily Transaction Volume",
    xaxis_title="Date",
    yaxis_title="Transaction Volume",
    legend_title="NFT Collections",
    autosize=False,
    width=1000,
    height=500
)

fig.show()
pyo.plot(fig, 
         filename = SAVE_DIR+f'TOTAL_TxnHistoryCompare.html',
         auto_open=False)


'../GeneratedData/Total/TOTAL_TxnHistoryCompare.html'

In [5]:
from collections import defaultdict
import datetime
import plotly.graph_objs as go
import os
import json
import pandas as pd
import plotly.express as px
import plotly.offline as pyo

DATA_DIR = f'../GeneratedData/'
nft_list = [folder_name for folder_name in os.listdir(DATA_DIR) if (folder_name != '.DS_Store') and (folder_name != 'Total')]

def get_daily_transaction_volume(txn_list):
    daily_transaction_count = defaultdict(int)
    for txn in txn_list:
        date = datetime.datetime.fromtimestamp(txn['timestamp']).strftime('%Y-%m-%d')
        daily_transaction_count[date] += 1
    return daily_transaction_count

def calculate_gas_costs(txn_list):
    gas_prices = [txn['gas_price'] for txn in txn_list]
    gas_used = [txn['gas_used'] for txn in txn_list]
    return [price * used for price, used in zip(gas_prices, gas_used)]

def calculate_avg_increase_time(txn_list):
    increase_times = []
    current_start_time = None
    for i in range(1, len(txn_list)):
        if txn_list[i]['gas_price'] > txn_list[i-1]['gas_price'] and current_start_time is None:
            current_start_time = txn_list[i]['timestamp']
        elif txn_list[i]['gas_price'] < txn_list[i-1]['gas_price'] and current_start_time is not None:
            increase_times.append(txn_list[i-1]['timestamp'] - current_start_time)
            current_start_time = None
    if current_start_time is not None:
        increase_times.append(txn_list[-1]['timestamp'] - current_start_time)
    return sum(increase_times) / len(increase_times) / 60

avg_volumes = []
avg_increase_times = []
costs_data = []

for nft_name in nft_list:
    for file_name in os.listdir(DATA_DIR + nft_name):
        if '.json' in file_name:
            with open(DATA_DIR + nft_name + "/" + file_name,'r') as file:
                json_data = file.read()
            txn_list = json.loads(json_data)
            
            # Calculate daily transaction volume for each NFT collection
            daily_txn_volume = get_daily_transaction_volume(txn_list)
            avg_volume = sum(daily_txn_volume.values()) / len(daily_txn_volume)
            avg_volumes.append({nft_name:avg_volume})

            # Calculate gas costs for each NFT collection
            costs = calculate_gas_costs(txn_list)
            costs_data.append(go.Scatter(y=costs, mode='lines', name=nft_name))

            # Calculate average increase time for each NFT collection
            avg_increase_time = calculate_avg_increase_time(txn_list)
            avg_increase_times.append(avg_increase_time)

# Show average volumes
print("Avg Volumes:")
for vol in avg_volumes:
    print(vol)

# Create graph for gas costs
fig = go.Figure()
for data in costs_data:
    fig.add_trace(data)
fig.update_layout(title="Gas Costs per Transaction", xaxis_title="Transaction Index", yaxis_title="Total Gas Cost")
fig.show()
pyo.plot(fig, 
         filename = SAVE_DIR+f'TOTAL_GasCostCompare.html',
         auto_open=False)

Avg Volumes:
{'BEANZ': 131.7714932126697}
{'MetaKongz': 42.18279569892473}


'../GeneratedData/Total/TOTAL_GasCostCompare.html'

In [6]:
nft_list

['BEANZ', 'MetaKongz']

In [7]:
# Create graph for average increase time
avg_increase_df = pd.DataFrame({
    'NFT': nft_list,
    'Average Increase Time (minutes)': avg_increase_times
})
fig = px.bar(avg_increase_df, x='NFT', y='Average Increase Time (minutes)', title="Average Time for Gas Cost to Start Decreasing")
fig.show()
pyo.plot(fig, 
         filename = SAVE_DIR+f'TOTAL_AvgDecreaseTime.html',
         auto_open=False)

'../GeneratedData/Total/TOTAL_AvgDecreaseTime.html'